In [ ]:
!pip install torch torchvision optuna
!git clone https://github.com/ultralytics/yolov5
%cd yolov5
!pip install -r requirements.txt

Cloning into 'yolov5'...
remote: Enumerating objects: 17022, done.
remote: Total 17022 (delta 0), reused 0 (delta 0), pack-reused 17022 (from 1)
Receiving objects: 100% (17022/17022), 15.61 MiB | 16.24 MiB/s, done.
Resolving deltas: 100% (11690/11690), done.
/content/yolov5/yolov5/yolov5


In [ ]:
!unrar x /content/coco128.rar


UNRAR 6.11 beta 1 freeware      Copyright (c) 1993-2022 Alexander Roshal

Unexpected end of archive

Extracting from /content/coco128.rar

Creating    coco128                                                   OK
Creating    coco128/test                                              OK
Creating    coco128/test/images                                       OK
Extracting  coco128/test/images/1004744.jpg                                0%  OK 
Extracting  coco128/test/images/1004963.jpg                                0%  OK 
Extracting  coco128/test/images/100864.jpg                                 0%  OK 
Extracting  coco128/test/images/1009072.jpg                                0%  OK 
Extracting  coco128/test/images/1011328.jpg                                0%  OK 
Extracting  coco128/test/images/101251.jpg                                 0%  OK 
Extracting  coco128/test/images/1013397.jpg                                0%  O

In [ ]:
!pip install optuna pyyaml

In [ ]:
import os
import tempfile
import yaml
import optuna
import pandas as pd
from yolov5 import train

def get_latest_map(save_dir):
    results_path = os.path.join(save_dir, 'results.csv')
    try:
        df = pd.read_csv(results_path)
        print(df.info())
        print("mAP_0.5: ",df['     metrics/mAP_0.5'])
        map50 = df['     metrics/mAP_0.5'].iloc[-1]

        return map50

    except (IndexError, ValueError, FileNotFoundError, KeyError) as e:
        print(f"Could not retrieve mAP@0.5 due to: {e}")

        return float('-inf')

default_hyp = {
    'lr0': 0.01,
    'lrf': 0.01,
    'momentum': 0.937,
    'weight_decay': 0.0005,
    'warmup_epochs': 3.0,
    'warmup_momentum': 0.8,
    'warmup_bias_lr': 0.1,
    'box': 0.05,
    'cls': 0.5,
    'cls_pw': 1.0,
    'obj': 1.0,
    'obj_pw': 1.0,
    'iou_t': 0.20,
    'anchor_t': 4.0,
    'fl_gamma': 0.0,
    'hsv_h': 0.015,
    'hsv_s': 0.7,
    'hsv_v': 0.4,
    'degrees': 0.0,
    'translate': 0.1,
    'scale': 0.5,
    'shear': 0.0,
    'perspective': 0.0,
    'flipud': 0.0,
    'fliplr': 0.5,
    'mosaic': 1.0,
    'mixup': 0.0,
    'copy_paste': 0.0
}

def objective(trial):

    hyp = default_hyp.copy()
    hyp['lr0'] = trial.suggest_float('lr0', 0.0001, 0.01, log=True)
    hyp['momentum'] = trial.suggest_float('momentum', 0.8, 0.95)
    hyp['weight_decay'] = trial.suggest_float('weight_decay', 0.0001, 0.01, log=True)

    with tempfile.NamedTemporaryFile(mode='w', suffix='.yaml', delete=False) as f:
        yaml.dump(hyp, f)
        hyp_path = f.name

    batch_size = trial.suggest_categorical('batch_size', [8, 16, 32])
    try:

        results = train.run(
            data='/content/yolov5/data/coco128.yaml',
            imgsz=512,
            epochs=20,
            weights='yolov5s.pt',
            batch=batch_size,
            hyp=hyp_path,
            project='runs/optuna',
            name=f'trial_{trial.number}'
        )

        os.unlink(hyp_path)

        save_dir = results.save_dir
        map50 = get_latest_map(save_dir)
        print(f"Trial {trial.number} - mAP@0.5: {map50:.4f}")
        return map50

    except Exception as e:
        print(f"Training failed with error: {e}")

        if 'hyp_path' in locals():
            os.unlink(hyp_path)
        return float('-inf')

def optimize_hyperparameters(n_trials=5):
    study = optuna.create_study(direction="maximize")
    study.optimize(objective, n_trials=n_trials)

    best_trial = study.best_trial
    best_params = default_hyp.copy()
    best_params.update(best_trial.params)

    print("\nBest trial:")
    print(f"  Value (mAP@0.5): {best_trial.value:.4f}")
    print("  Params: ")
    for key, value in best_params.items():
        print(f"    {key}: {value}")

    return best_params


Creating new Ultralytics Settings v0.0.6 file ✅ 
View Ultralytics Settings with 'yolo settings' or at '/root/.config/Ultralytics/settings.json'
Update Settings with 'yolo settings key=value', i.e. 'yolo settings runs_dir=path/to/dir'. For help see https://docs.ultralytics.com/quickstart/#ultralytics-settings.


wandb: WARNING ⚠️ wandb is deprecated and will be removed in a future release. See supported integrations at https://github.com/ultralytics/yolov5#integrations.
wandb: Using wandb-core as the SDK backend. Please refer to https://wandb.me/wandb-core for more information.


<IPython.core.display.Javascript object>

wandb: (1) Create a W&B account
wandb: (2) Use an existing W&B account
wandb: (3) Don't visualize my results


wandb: Enter your choice: (30 second timeout) 3


wandb: You chose "Don't visualize my results"


In [ ]:
if __name__ == "__main__":
    best_hyperparameters = optimize_hyperparameters(n_trials=5)

    with tempfile.NamedTemporaryFile(mode='w', suffix='.yaml', delete=False) as f:
        yaml.dump(best_hyperparameters, f)
        final_hyp_path = f.name

    try:
        final_results = train.run(
            data='/content/yolov5/data/coco128.yaml',
            imgsz=512,
            epochs=20,
            weights='yolov5s.pt',
            batch=best_hyperparameters['batch_size'],
            hyp=final_hyp_path
        )
    finally:
        os.unlink(final_hyp_path)

[I 2024-10-29 21:20:56,529] A new study created in memory with name: no-name-587ef4b1-ed28-43d2-9aec-812fdb8136d1
train: weights=yolov5s.pt, cfg=, data=/content/yolov5/data/coco128.yaml, hyp=/tmp/tmp3te5juaf.yaml, epochs=20, batch_size=16, imgsz=512, rect=False, resume=False, nosave=False, noval=False, noautoanchor=False, noplots=False, evolve=None, evolve_population=data/hyps, resume_evolve=None, bucket=, cache=None, image_weights=False, device=, multi_scale=False, single_cls=False, optimizer=SGD, sync_bn=False, workers=8, project=runs/optuna, name=trial_0, exist_ok=False, quad=False, cos_lr=False, label_smoothing=0.0, patience=100, freeze=[0], save_period=-1, seed=0, local_rank=-1, entity=None, upload_dataset=False, bbox_interval=-1, artifact_alias=latest, ndjson_console=False, ndjson_file=False, batch=32
github: up to date with https://github.com/ultralytics/yolov5 ✅
YOLOv5 🚀 v7.0-378-g2f74455a Python-3.10.12 torch-2.5.0+cu121 CUDA:0 (Tesla T4, 15102MiB)

hyperparameters: anchor_t=4

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 20 entries, 0 to 19
Data columns (total 14 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0                  epoch  20 non-null     int64  
 1         train/box_loss  20 non-null     float64
 2         train/obj_loss  20 non-null     float64
 3         train/cls_loss  20 non-null     float64
 4      metrics/precision  20 non-null     float64
 5         metrics/recall  20 non-null     float64
 6        metrics/mAP_0.5  20 non-null     float64
 7   metrics/mAP_0.5:0.95  20 non-null     float64
 8           val/box_loss  20 non-null     float64
 9           val/obj_loss  20 non-null     float64
 10          val/cls_loss  20 non-null     float64
 11                 x/lr0  20 non-null     float64
 12                 x/lr1  20 non-null     float64
 13                 x/lr2  20 non-null     float64
dtypes: float64(13), int64(1)
memory usage: 2.3 KB
None
mAP_0.5:  0     0.074711


github: up to date with https://github.com/ultralytics/yolov5 ✅
YOLOv5 🚀 v7.0-378-g2f74455a Python-3.10.12 torch-2.5.0+cu121 CUDA:0 (Tesla T4, 15102MiB)

hyperparameters: anchor_t=4.0, box=0.05, cls=0.5, cls_pw=1.0, copy_paste=0.0, degrees=0.0, fl_gamma=0.0, fliplr=0.5, flipud=0.0, hsv_h=0.015, hsv_s=0.7, hsv_v=0.4, iou_t=0.2, lr0=0.000773736135649755, lrf=0.01, mixup=0.0, momentum=0.8052756699641026, mosaic=1.0, obj=1.0, obj_pw=1.0, perspective=0.0, scale=0.5, shear=0.0, translate=0.1, warmup_bias_lr=0.1, warmup_epochs=3.0, warmup_momentum=0.8, weight_decay=0.0003123578368422968
Comet: run 'pip install comet_ml' to automatically track and visualize YOLOv5 🚀 runs in Comet
TensorBoard: Start with 'tensorboard --logdir runs/optuna', view at http://localhost:6006/
Overriding model.yaml nc=80 with nc=10

                 from  n    params  module                                  arguments                     
  0                -1  1      3520  models.common.Conv                      [3, 3

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 20 entries, 0 to 19
Data columns (total 14 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0                  epoch  20 non-null     int64  
 1         train/box_loss  20 non-null     float64
 2         train/obj_loss  20 non-null     float64
 3         train/cls_loss  20 non-null     float64
 4      metrics/precision  20 non-null     float64
 5         metrics/recall  20 non-null     float64
 6        metrics/mAP_0.5  20 non-null     float64
 7   metrics/mAP_0.5:0.95  20 non-null     float64
 8           val/box_loss  20 non-null     float64
 9           val/obj_loss  20 non-null     float64
 10          val/cls_loss  20 non-null     float64
 11                 x/lr0  20 non-null     float64
 12                 x/lr1  20 non-null     float64
 13                 x/lr2  20 non-null     float64
dtypes: float64(13), int64(1)
memory usage: 2.3 KB
None
mAP_0.5:  0     0.003561


github: up to date with https://github.com/ultralytics/yolov5 ✅
YOLOv5 🚀 v7.0-378-g2f74455a Python-3.10.12 torch-2.5.0+cu121 CUDA:0 (Tesla T4, 15102MiB)

hyperparameters: anchor_t=4.0, box=0.05, cls=0.5, cls_pw=1.0, copy_paste=0.0, degrees=0.0, fl_gamma=0.0, fliplr=0.5, flipud=0.0, hsv_h=0.015, hsv_s=0.7, hsv_v=0.4, iou_t=0.2, lr0=0.0011922448552460045, lrf=0.01, mixup=0.0, momentum=0.9081830453108048, mosaic=1.0, obj=1.0, obj_pw=1.0, perspective=0.0, scale=0.5, shear=0.0, translate=0.1, warmup_bias_lr=0.1, warmup_epochs=3.0, warmup_momentum=0.8, weight_decay=0.0029114014405807647
Comet: run 'pip install comet_ml' to automatically track and visualize YOLOv5 🚀 runs in Comet
TensorBoard: Start with 'tensorboard --logdir runs/optuna', view at http://localhost:6006/
Overriding model.yaml nc=80 with nc=10

                 from  n    params  module                                  arguments                     
  0                -1  1      3520  models.common.Conv                      [3, 

...

github: up to date with https://github.com/ultralytics/yolov5 ✅
YOLOv5 🚀 v7.0-378-g2f74455a Python-3.10.12 torch-2.5.0+cu121 CUDA:0 (Tesla T4, 15102MiB)

hyperparameters: anchor_t=4.0, box=0.05, cls=0.5, cls_pw=1.0, copy_paste=0.0, degrees=0.0, fl_gamma=0.0, fliplr=0.5, flipud=0.0, hsv_h=0.015, hsv_s=0.7, hsv_v=0.4, iou_t=0.2, lr0=0.00015696116260225775, lrf=0.01, mixup=0.0, momentum=0.9475729639346845, mosaic=1.0, obj=1.0, obj_pw=1.0, perspective=0.0, scale=0.5, shear=0.0, translate=0.1, warmup_bias_lr=0.1, warmup_epochs=3.0, warmup_momentum=0.8, weight_decay=0.0010813979674285602
Comet: run 'pip install comet_ml' to automatically track and visualize YOLOv5 🚀 runs in Comet
TensorBoard: Start with 'tensorboard --logdir runs/optuna', view at http://localhost:6006/
Overriding model.yaml nc=80 with nc=10

                 from  n    params  module                                  arguments                     
  0                -1  1      3520  models.common.Conv                      [3,

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 20 entries, 0 to 19
Data columns (total 14 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0                  epoch  20 non-null     int64  
 1         train/box_loss  20 non-null     float64
 2         train/obj_loss  20 non-null     float64
 3         train/cls_loss  20 non-null     float64
 4      metrics/precision  20 non-null     float64
 5         metrics/recall  20 non-null     float64
 6        metrics/mAP_0.5  20 non-null     float64
 7   metrics/mAP_0.5:0.95  20 non-null     float64
 8           val/box_loss  20 non-null     float64
 9           val/obj_loss  20 non-null     float64
 10          val/cls_loss  20 non-null     float64
 11                 x/lr0  20 non-null     float64
 12                 x/lr1  20 non-null     float64
 13                 x/lr2  20 non-null     float64
dtypes: float64(13), int64(1)
memory usage: 2.3 KB
None
mAP_0.5:  0     0.002178


github: up to date with https://github.com/ultralytics/yolov5 ✅
YOLOv5 🚀 v7.0-378-g2f74455a Python-3.10.12 torch-2.5.0+cu121 CUDA:0 (Tesla T4, 15102MiB)

hyperparameters: anchor_t=4.0, box=0.05, cls=0.5, cls_pw=1.0, copy_paste=0.0, degrees=0.0, fl_gamma=0.0, fliplr=0.5, flipud=0.0, hsv_h=0.015, hsv_s=0.7, hsv_v=0.4, iou_t=0.2, lr0=0.00045973461861933566, lrf=0.01, mixup=0.0, momentum=0.8051462498321699, mosaic=1.0, obj=1.0, obj_pw=1.0, perspective=0.0, scale=0.5, shear=0.0, translate=0.1, warmup_bias_lr=0.1, warmup_epochs=3.0, warmup_momentum=0.8, weight_decay=0.00016469701274370786
Comet: run 'pip install comet_ml' to automatically track and visualize YOLOv5 🚀 runs in Comet
TensorBoard: Start with 'tensorboard --logdir runs/optuna', view at http://localhost:6006/
Overriding model.yaml nc=80 with nc=10

                 from  n    params  module                                  arguments                     
  0                -1  1      3520  models.common.Conv                      [3

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 20 entries, 0 to 19
Data columns (total 14 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0                  epoch  20 non-null     int64  
 1         train/box_loss  20 non-null     float64
 2         train/obj_loss  20 non-null     float64
 3         train/cls_loss  20 non-null     float64
 4      metrics/precision  20 non-null     float64
 5         metrics/recall  20 non-null     float64
 6        metrics/mAP_0.5  20 non-null     float64
 7   metrics/mAP_0.5:0.95  20 non-null     float64
 8           val/box_loss  20 non-null     float64
 9           val/obj_loss  20 non-null     float64
 10          val/cls_loss  20 non-null     float64
 11                 x/lr0  20 non-null     float64
 12                 x/lr1  20 non-null     float64
 13                 x/lr2  20 non-null     float64
dtypes: float64(13), int64(1)
memory usage: 2.3 KB
None
mAP_0.5:  0     0.002487


github: up to date with https://github.com/ultralytics/yolov5 ✅
YOLOv5 🚀 v7.0-378-g2f74455a Python-3.10.12 torch-2.5.0+cu121 CUDA:0 (Tesla T4, 15102MiB)

hyperparameters: anchor_t=4.0, batch_size=32, box=0.05, cls=0.5, cls_pw=1.0, copy_paste=0.0, degrees=0.0, fl_gamma=0.0, fliplr=0.5, flipud=0.0, hsv_h=0.015, hsv_s=0.7, hsv_v=0.4, iou_t=0.2, lr0=0.007036060630756563, lrf=0.01, mixup=0.0, momentum=0.9082176349361591, mosaic=1.0, obj=1.0, obj_pw=1.0, perspective=0.0, scale=0.5, shear=0.0, translate=0.1, warmup_bias_lr=0.1, warmup_epochs=3.0, warmup_momentum=0.8, weight_decay=0.0008887147729046771
Comet: run 'pip install comet_ml' to automatically track and visualize YOLOv5 🚀 runs in Comet
TensorBoard: Start with 'tensorboard --logdir runs/train', view at http://localhost:6006/
Overriding model.yaml nc=80 with nc=10

                 from  n    params  module                                  arguments                     
  0                -1  1      3520  models.common.Conv             

In [ ]:
!python /content/yolov5/val.py --data /content/yolov5/data/coco128.yaml --weights /content/yolov5/runs/train/exp/weights/best.pt --task test


val: data=/content/yolov5/data/coco128.yaml, weights=['/content/yolov5/runs/train/exp/weights/best.pt'], batch_size=32, imgsz=640, conf_thres=0.001, iou_thres=0.6, max_det=300, task=test, device=, workers=8, single_cls=False, augment=False, verbose=False, save_txt=False, save_hybrid=False, save_conf=False, save_json=False, project=runs/val, name=exp, exist_ok=False, half=False, dnn=False
YOLOv5 🚀 v7.0-378-g2f74455a Python-3.10.12 torch-2.5.0+cu121 CUDA:0 (Tesla T4, 15102MiB)

Fusing layers... 
Model summary: 157 layers, 7037095 parameters, 0 gradients, 15.8 GFLOPs
test: Scanning /content/yolov5/coco128/test/labels... 250 images, 0 backgrounds, 0 corrupt: 100% 250/250 [00:00<00:00, 509.05it/s]
test: New cache created: /content/yolov5/coco128/test/labels.cache
                 Class     Images  Instances          P          R      mAP50   mAP50-95: 100% 8/8 [00:08<00:00,  1.00s/it]
                   all        250        336      0.487       0.55      0.518      0.357
             apple

In [ ]:
!python /content/yolov5/detect.py --source /content/test1.jpg --weights /content/yolov5/runs/train/exp/weights/best.pt


detect: weights=['/content/yolov5/runs/train/exp/weights/best.pt'], source=/content/test1.jpg, data=data/coco128.yaml, imgsz=[640, 640], conf_thres=0.25, iou_thres=0.45, max_det=1000, device=, view_img=False, save_txt=False, save_format=0, save_csv=False, save_conf=False, save_crop=False, nosave=False, classes=None, agnostic_nms=False, augment=False, visualize=False, update=False, project=runs/detect, name=exp, exist_ok=False, line_thickness=3, hide_labels=False, hide_conf=False, half=False, dnn=False, vid_stride=1
YOLOv5 🚀 v7.0-378-g2f74455a Python-3.10.12 torch-2.5.0+cu121 CUDA:0 (Tesla T4, 15102MiB)

Fusing layers... 
Model summary: 157 layers, 7037095 parameters, 0 gradients, 15.8 GFLOPs
WARNING ⚠️ NMS time limit 0.550s exceeded
image 1/1 /content/test1.jpg: 384x640 1 tiramisu, 41.6ms
Speed: 0.5ms pre-process, 41.6ms inference, 897.7ms NMS per image at shape (1, 3, 640, 640)
Results saved to runs/detect/exp


In [ ]:
!python /content/yolov5/detect.py --source /content/test2.jpg --weights /content/yolov5/runs/train/exp/weights/best.pt

detect: weights=['/content/yolov5/runs/train/exp/weights/best.pt'], source=/content/test2.jpg, data=data/coco128.yaml, imgsz=[640, 640], conf_thres=0.25, iou_thres=0.45, max_det=1000, device=, view_img=False, save_txt=False, save_format=0, save_csv=False, save_conf=False, save_crop=False, nosave=False, classes=None, agnostic_nms=False, augment=False, visualize=False, update=False, project=runs/detect, name=exp, exist_ok=False, line_thickness=3, hide_labels=False, hide_conf=False, half=False, dnn=False, vid_stride=1
YOLOv5 🚀 v7.0-378-g2f74455a Python-3.10.12 torch-2.5.0+cu121 CUDA:0 (Tesla T4, 15102MiB)

Fusing layers... 
Model summary: 157 layers, 7037095 parameters, 0 gradients, 15.8 GFLOPs
WARNING ⚠️ NMS time limit 0.550s exceeded
image 1/1 /content/test2.jpg: 448x640 1 cannoli, 3 edamames, 1 ramen, 27.6ms
Speed: 0.6ms pre-process, 27.6ms inference, 566.7ms NMS per image at shape (1, 3, 640, 640)
Results saved to runs/detect/exp2
